In [1]:
%cd /workspace/working
!git clone https://github.com/mistralai/mistral-finetune.git

/workspace/working
Cloning into 'mistral-finetune'...


/workspace/working/venv/lib/python3.10/site-packages/IPython/core/magics/osm.py:417: UserWarning: This is now an optional IPython functionality, setting dhist requires you to install the `pickleshare` library.
  self.shell.db['dhist'] = compress_dhist(dhist)[-100:]


remote: Enumerating objects: 472, done.
remote: Counting objects: 100% (249/249), done.
remote: Compressing objects: 100% (90/90), done.
remote: Total 472 (delta 211), reused 159 (delta 159), pack-reused 223 (from 2)
Receiving objects: 100% (472/472), 243.32 KiB | 5.29 MiB/s, done.
Resolving deltas: 100% (251/251), done.


In [2]:
# %pip install -r /workspace/working/mistral-finetune/requirements.txt

In [3]:
# %pip install huggingface_hub

In [4]:
# !pip install -q llama-cpp-python --extra-index-url https://abetlen.github.io/llama-cpp-python/whl/cu121

In [5]:
from huggingface_hub import snapshot_download
from pathlib import Path

# Set the path to the /workspace/working directory
mistral_models_path = Path('/workspace/working/', 'mistral_models')
mistral_models_path.mkdir(parents=True, exist_ok=True)

# Download model snapshot to the desired path
snapshot_download(repo_id="mistralai/Mistral-7B-Instruct-v0.3", allow_patterns=["params.json", "consolidated.safetensors", "tokenizer.model.v3"], local_dir=mistral_models_path)
# snapshot_download(repo_id="unsloth/mistral-7b-instruct-v0.3-bnb-4bit", allow_patterns=["config.json", "model.safetensors", "tokenizer.model.v3"], local_dir=mistral_models_path)

# import json

# # Create a dictionary (or any other data structure)
# data = {
#     "dim": 4096,
#     "n_layers": 32,
#     "head_dim": 128,
#     "hidden_dim": 14336,
#     "n_heads": 32,
#     "n_kv_heads": 8,
#     "norm_eps": 1e-05,
#     "vocab_size": 32768,
#     "rope_theta": 1000000.0
# }

# Specify the path where the file will be saved
# file_path = '/workspace/working/mistral_models/params.json'

# # Write the dictionary to a JSON file
# with open(file_path, 'w') as json_file:
#     json.dump(data, json_file, indent=4)

# print(f"JSON file created at {file_path}")

# os.rename('/workspace/working/mistral_models/model.safetensors', '/workspace/working/mistral_models/consolidated.safetensors')

# Copy the model files to the /workspace/working directory (if necessary)
# !mv /workspace/working/mistral_models/7B-instruct-v0.3 /workspace/working/mistral_models
# !rm -r /workspace/working/mistral_models/7B-instruct-v0.3


Fetching 3 files:   0%|          | 0/3 [00:00<?, ?it/s]

consolidated.safetensors:   0%|          | 0.00/14.5G [00:00<?, ?B/s]

tokenizer.model.v3:   0%|          | 0.00/587k [00:00<?, ?B/s]

params.json:   0%|          | 0.00/202 [00:00<?, ?B/s]

'/workspace/working/mistral_models'

In [1]:
%ls /workspace/working/mistral_models/

consolidated.safetensors  params.json  tokenizer.model.v3


In [2]:
%cd /workspace/working/

/workspace/working


/workspace/working/venv/lib/python3.10/site-packages/IPython/core/magics/osm.py:417: UserWarning: This is now an optional IPython functionality, setting dhist requires you to install the `pickleshare` library.
  self.shell.db['dhist'] = compress_dhist(dhist)[-100:]


In [3]:
%mkdir -p data

In [4]:
%cd /workspace/working/data/

/workspace/working/data


In [5]:
import pandas as pd
import copy
df = pd.read_parquet("hf://datasets/julioc-p/Question-Sparql/data/train-00000-of-00001.parquet")
dftemp = df.copy()
dftemp

text_query language  \
0       Welche Bücher von Kerouac wurden von Viking Pr...       de   
1       ¿Qué libros de Kerouac han sido publicados por...       es   
2       Quali libri di Kerouac furono pubblicati da Vi...       it   
3       Quels lives de Kerouac ont été publiés par Vik...       fr   
4       Welke boeken van Jack Kerouac werden uitgegeve...       nl   
...                                                   ...      ...   
893476  Was sind die Arten von Speisen oder Gerichten,...       de   
893477  Welche Art von Essen oder Gericht enthält das ...       de   
893478  Welche Art von Quantenteilchen hat das höchste...       de   
893479  Welches Quantenteilchen hat das höchste Gyroma...       de   
893480  Sage mir die literarische Gattung, deren Name ...       de   

                                             sparql_query knowledge_graphs  
0       PREFIX dbo: <http://dbpedia.org/ontology/>\nPR...          DBpedia  
1       PREFIX dbo: <http://dbpedia.org/ontology/>\nPR...          DBpedia  
2       PREFIX dbo: <http://dbpedia.org/ontology/>\nPR...          DBpedia  
3       PREFIX dbo: <http://dbpedia.org/ontology/>\nPR...          DBpedia  
4       PREFIX dbo: <http://dbpedia.org/ontology/>\nPR...          DBpedia  
...                                                   ...              ...  
893476  SELECT DISTINCT ?sbj ?sbj_label { ?statement1 ...          DBpedia  
893477  SELECT DISTINCT ?sbj ?sbj_label { ?statement1 ...          DBpedia  
893478  select ?ent where {\n?ent <http://www.wikidata...          DBpedia  
893479  select ?ent where {\n?ent <http://www.wikidata...          DBpedia  
893480  SELECT DISTINCT ?sbj ?sbj_label { ?statement1 ...          DBpedia  

[893481 rows x 4 columns]

In [6]:
dftemp = dftemp[dftemp["language"] == "en"]
dftemp = dftemp[dftemp["knowledge_graphs"] == "DBpedia"]
dftemp[dftemp["language"] != "en"]
# dftemp

Empty DataFrame
Columns: [text_query, language, sparql_query, knowledge_graphs]
Index: []

In [7]:
dftemp[dftemp["knowledge_graphs"] != "DBpedia"]

Empty DataFrame
Columns: [text_query, language, sparql_query, knowledge_graphs]
Index: []

In [8]:
dftemp.reset_index(drop = True, inplace = True)
dftemp.drop(columns=["language", "knowledge_graphs"], axis = 1, inplace = True)
tbremovedrows = dftemp["sparql_query"].str.contains("\n")
dftemp = dftemp[~tbremovedrows]
dftemp.reset_index(drop = True, inplace = True)
dftemp["messages"] = dftemp.apply(lambda row: [{"role": "user", "content": row["text_query"]}, {"role": "assistant", "content": row["sparql_query"]}], axis=1)
dftemp.rename(columns = {"text_query" : "NL_Query"}, inplace = True)
dftemp.drop(columns = "sparql_query", inplace = True)

In [9]:
dftemp

NL_Query  \
0                 How high is the lighthouse in Colombo?   
1          Who is the host of the BBC Wildlife Specials?   
2                        How much did Pulp Fiction cost?   
3                  In what city is the Heineken brewery?   
4                  When did Operation Overlord commence?   
...                                                  ...   
42233                  Name a gene that begins with a T.   
42234  What is antonym of of spore print color of Ple...   
42235  Tell me mixture whose name has the word spirom...   
42236  Let me know blend whose title has the word spi...   
42237          What Theoi Project ID does Manticore has?   

                                                messages  
0      [{'role': 'user', 'content': 'How high is the ...  
1      [{'role': 'user', 'content': 'Who is the host ...  
2      [{'role': 'user', 'content': 'How much did Pul...  
3      [{'role': 'user', 'content': 'In what city is ...  
4      [{'role': 'user', 'content': 'When did Operati...  
...                                                  ...  
42233  [{'role': 'user', 'content': 'Name a gene that...  
42234  [{'role': 'user', 'content': 'What is antonym ...  
42235  [{'role': 'user', 'content': 'Tell me mixture ...  
42236  [{'role': 'user', 'content': 'Let me know blen...  
42237  [{'role': 'user', 'content': 'What Theoi Proje...  

[42238 rows x 2 columns]

In [10]:
print(dftemp["NL_Query"].str.len().max())
print(dftemp["messages"].str.len().max())
print(
    dftemp["messages"]
    .apply(lambda x: " ".join([msg.get("content", "") for msg in x if msg.get("role") == "assistant"]) if isinstance(x, list) else "")
    .str.len()
    .max()
)

434
2
826


In [11]:
df_train=dftemp.sample(frac=0.80,random_state=200)
df_eval=dftemp.drop(df_train.index)

df_train.reset_index(drop = True, inplace = True)
df_eval.reset_index(drop = True, inplace = True)
df_train

NL_Query  \
0      What is the sister city of the birthplace of N...   
1       Is the oxidation state of phosphorus equal to 3?   
2      Where is the official residence and the office...   
3      WHICH IS THE SUBSIDIARY COMPANY OF SHAREHOLDER...   
4            What is  in the performer of Vivien Leigh ?   
...                                                  ...   
33785  What are the national symbol which start with ...   
33786                    What is the Xbox One Connector?   
33787   Is 0 the the number of houses of the Schuleroch?   
33788  Whichs {house} of {characters} of {Benvenuto C...   
33789  List all the locations of the companies whose ...   

                                                messages  
0      [{'role': 'user', 'content': 'What is the sist...  
1      [{'role': 'user', 'content': 'Is the oxidation...  
2      [{'role': 'user', 'content': 'Where is the off...  
3      [{'role': 'user', 'content': 'WHICH IS THE SUB...  
4      [{'role': 'user', 'content': 'What is  in the ...  
...                                                  ...  
33785  [{'role': 'user', 'content': 'What are the nat...  
33786  [{'role': 'user', 'content': 'What is the Xbox...  
33787  [{'role': 'user', 'content': 'Is 0 the the num...  
33788  [{'role': 'user', 'content': 'Whichs {house} o...  
33789  [{'role': 'user', 'content': 'List all the loc...  

[33790 rows x 2 columns]

In [12]:
df_eval

NL_Query  \
0                       How much did Pulp Fiction cost?   
1                 In what city is the Heineken brewery?   
2                 When did Operation Overlord commence?   
3            In which city does the Chile Route 68 end?   
4                          Where does Piccadilly start?   
...                                                 ...   
8443  True or False: Kenya's Human Development Index...   
8444   Who wrote the bibiiography of Natja Brunckhorst?   
8445  What are the jurisdiction which start with the...   
8446  what are the emirate of the united arab emirat...   
8447                  Name a gene that begins with a T.   

                                               messages  
0     [{'role': 'user', 'content': 'How much did Pul...  
1     [{'role': 'user', 'content': 'In what city is ...  
2     [{'role': 'user', 'content': 'When did Operati...  
3     [{'role': 'user', 'content': 'In which city do...  
4     [{'role': 'user', 'content': 'Where does Picca...  
...                                                 ...  
8443  [{'role': 'user', 'content': 'True or False: K...  
8444  [{'role': 'user', 'content': 'Who wrote the bi...  
8445  [{'role': 'user', 'content': 'What are the jur...  
8446  [{'role': 'user', 'content': 'what are the emi...  
8447  [{'role': 'user', 'content': 'Name a gene that...  

[8448 rows x 2 columns]

In [13]:
print(df_train.iloc[0]["NL_Query"])
df_train.iloc[0]["messages"]

What is the sister city of the birthplace of Nikita Telenkov?


[{'role': 'user',
  'content': 'What is the sister city of the birthplace of Nikita Telenkov?'},
 {'role': 'assistant',
  'content': 'SELECT ?answer WHERE { ?statement1 <http://www.w3.org/1999/02/22-rdf-syntax-ns#subject> <http://wikidata.dbpedia.org/resource/Q7035115> . ?statement1 <http://www.w3.org/1999/02/22-rdf-syntax-ns#predicate> <http://www.wikidata.org/entity/P19>. ?statement1 <http://www.w3.org/1999/02/22-rdf-syntax-ns#object> ?X . ?statement2 <http://www.w3.org/1999/02/22-rdf-syntax-ns#subject> ?X. ?statement2 <http://www.w3.org/1999/02/22-rdf-syntax-ns#predicate> <http://www.wikidata.org/entity/P190> . ?statement2 <http://www.w3.org/1999/02/22-rdf-syntax-ns#object> ?answer . }'}]

In [14]:
# save data into .jsonl files
df_train.to_json("NL_to_SPARQL_train.jsonl", orient="records", lines=True)
df_eval.to_json("NL_to_SPARQL_eval.jsonl", orient="records", lines=True)

In [15]:
%ls /workspace/working/data/

NL_to_SPARQL_eval.jsonl  NL_to_SPARQL_train.jsonl


In [16]:
%cd /workspace/working/mistral-finetune/

/workspace/working/mistral-finetune


/workspace/working/venv/lib/python3.10/site-packages/IPython/core/magics/osm.py:417: UserWarning: This is now an optional IPython functionality, setting dhist requires you to install the `pickleshare` library.
  self.shell.db['dhist'] = compress_dhist(dhist)[-100:]


In [17]:
import yaml

# # Read the existing YAML file
# with open('example/7B.yaml', 'r') as file:
#     data = yaml.safe_load(file)

# # Print the loaded data to see its contents
# print(data)

In [18]:
# # Modify the data
# data['data']['instruct_data'] = '/workspace/working/data/NL_to_SPARQL_train.jsonl'
# data['data']['eval_instruct_data'] = '/workspace/working/data/NL_to_SPARQL_eval.jsonl'
# data['model_id_or_path'] = '/workspace/working/mistral_models'
# data['run_dir'] = '/workspace/working/outputs'
# data['seq_len'] = 8192
# data['lora']['rank'] = 16
# data['log_freq'] = 50
# data['num_microbatches'] = 8
# data['optim']['lr'] = 1.e-5
# data['lora']['scaling'] = 16
# if 'wandb' in data:
#     del data['wandb']
# # data['wandb']['offline'] = True


# # Print the modified data
# print(data)
config = """
# data
data:
  instruct_data: "/workspace/working/data/NL_to_SPARQL_train.jsonl"  # Fill
  data: ""  # Optionally fill with pretraining data
  eval_instruct_data: "/workspace/working/data/NL_to_SPARQL_eval.jsonl"  # Optionally fill

# model
model_id_or_path: "/workspace/working/mistral_models"  # Change to downloaded path
lora:
  rank: 16
  scaling: 16
# optim
# tokens per training steps = batch_size x num_GPUs x seq_len
# we recommend sequence length of 32768
# If you run into memory error, you can try reduce the sequence length
seq_len: 2048
batch_size: 1
num_microbatches: 8
max_steps: 300
optim:
  lr: 1.e-5
  weight_decay: 0.1
  pct_start: 0.05

# other
seed: 0
log_freq: 10
eval_freq: 100
no_eval: False
ckpt_freq: 100

save_adapters: True  # save only trained LoRA adapters. Set to `False` to merge LoRA adapter into the base model and save full fine-tuned model

run_dir: "outputs"  # Fill
"""

# save the same file locally into the example.yaml file
import yaml
with open('example/7B.yaml', 'w') as file:
    yaml.dump(yaml.safe_load(config), file)

In [19]:
# config = """
# wandb:
#   offline: True
#   """
# # Write the modified data back to the file
# with open('example/7B.yaml', 'w') as file:
#     yaml.dump(data, file, default_flow_style=False)
#     file.write(config)

# print("YAML file updated successfully.")

In [20]:
! cat example/7B.yaml

batch_size: 1
ckpt_freq: 100
data:
  data: ''
  eval_instruct_data: /workspace/working/data/NL_to_SPARQL_eval.jsonl
  instruct_data: /workspace/working/data/NL_to_SPARQL_train.jsonl
eval_freq: 100
log_freq: 10
lora:
  rank: 16
  scaling: 16
max_steps: 300
model_id_or_path: /workspace/working/mistral_models
no_eval: false
num_microbatches: 8
optim:
  lr: 1.0e-05
  pct_start: 0.05
  weight_decay: 0.1
run_dir: outputs
save_adapters: true
seed: 0
seq_len: 2048


In [21]:
import os

print(os.path.exists("example/7B.yaml"))


True


In [22]:
%cd /workspace/working/mistral-finetune/

/workspace/working/mistral-finetune


In [23]:
!python -m utils.reformat_data /workspace/working/data/NL_to_SPARQL_train.jsonl

In [24]:
!python -m utils.reformat_data /workspace/working/data/NL_to_SPARQL_eval.jsonl

In [25]:
!python -m utils.validate_data --train_yaml example/7B.yaml

0it [00:00, ?it/s]Validating /workspace/working/data/NL_to_SPARQL_train.jsonl ...

100%|███████████████████████████████████| 33790/33790 [00:08<00:00, 4158.60it/s]
1it [00:08,  8.15s/it]
No errors! Data is correctly formatted!
Stats for /workspace/working/data/NL_to_SPARQL_train.jsonl 
 -------------------- 
 {
    "expected": {
        "eta": "00:06:47",
        "data_tokens": 7990855,
        "train_tokens": 4915200,
        "epochs": "0.62",
        "max_steps": 300,
        "data_tokens_per_dataset": {
            "/workspace/working/data/NL_to_SPARQL_train.jsonl": "7990855.0"
        },
        "train_tokens_per_dataset": {
            "/workspace/working/data/NL_to_SPARQL_train.jsonl": "4915200.0"
        },
        "epochs_per_dataset": {
            "/workspace/working/data/NL_to_SPARQL_train.jsonl": "0.6"
        }
    }
}
0it [00:00, ?it/s]Validating /workspace/working/data/NL_to_SPARQL_eval.jsonl ...

100%|█████████████████████████████████████| 8448/8448 [00:02<00:00, 4153.8

In [26]:
! cat example/7B.yaml

batch_size: 1
ckpt_freq: 100
data:
  data: ''
  eval_instruct_data: /workspace/working/data/NL_to_SPARQL_eval.jsonl
  instruct_data: /workspace/working/data/NL_to_SPARQL_train.jsonl
eval_freq: 100
log_freq: 10
lora:
  rank: 16
  scaling: 16
max_steps: 300
model_id_or_path: /workspace/working/mistral_models
no_eval: false
num_microbatches: 8
optim:
  lr: 1.0e-05
  pct_start: 0.05
  weight_decay: 0.1
run_dir: outputs
save_adapters: true
seed: 0
seq_len: 2048


In [27]:
!python -m utils.reformat_data /workspace/working/data/NL_to_SPARQL_train.jsonl

In [28]:
!python -m utils.reformat_data /workspace/working/data/NL_to_SPARQL_eval.jsonl

In [29]:
import torch
print("Number of GPUs Available:", torch.cuda.device_count())
for i in range(torch.cuda.device_count()):
    print(f"GPU {i}: {torch.cuda.get_device_name(i)}")

import torch
print(torch.cuda.get_device_name())  # Should show your GPU (e.g., Tesla T4)
print(torch.cuda.is_bf16_supported())  # Should be False (T4 doesn't support BF16)
print(torch.backends.cuda.matmul.allow_fp16_reduced_precision_reduction)  # Should be True (T4 supports FP16)

!nvidia-smi

Number of GPUs Available: 1
GPU 0: NVIDIA A800 80GB PCIe
NVIDIA A800 80GB PCIe
True
True
Thu Mar 27 23:57:52 2025       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 550.90.07              Driver Version: 550.90.07      CUDA Version: 12.4     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  NVIDIA A800 80GB PCIe          On  |   00000000:61:00.0 Off |                    0 |
| N/A   34C    P0             42W /  300W |       4MiB /  81920MiB |      0%      Default |
|                                         |        

In [30]:
# these info is needed for training
import os
os.environ["CUDA_DEVICE_ORDER"]="PCI_BUS_ID"
os.environ["CUDA_VISIBLE_DEVICES"]="0"

torch.cuda.empty_cache()

In [31]:
! cat train.py

import dataclasses
import logging
import os
import pprint
from contextlib import ExitStack
from pathlib import Path
from typing import TYPE_CHECKING

import fire
import torch.cuda
import torch.distributed as dist
from mistral_common.tokens.tokenizers.mistral import MistralTokenizer
from torch.optim import AdamW, lr_scheduler

from finetune.args import TrainArgs
from finetune.checkpointing import Checkpointer
from finetune.data.data_loader import build_data_loader
from finetune.distributed import (
    BACKEND,
    avg_aggregate,
    get_rank,
    get_world_size,
    is_torchrun,
    set_device,
)
from finetune.eval import evaluate
from finetune.loss import compute_loss_with_mask
from finetune.mixed_precision import (
    downcast_mixed_precision,
    prepare_mixed_precision,
    upcast_mixed_precision,
)
from finetune.monitoring.metrics_logger import (
    MetricsLogger,
    eval_log_msg,
    get_eval_logs,
    get_train_logs,
    train_log_msg,
)
from finetune.monitoring.utils import 

In [32]:
# with open("train.py", "r") as f:
#     content = f.read()

# # Modify content (e.g., replace dtype settings)
# content = content.replace("torch.bfloat16", "torch.float16")

# # Write back
# with open("train.py", "w") as f:
#     f.write(content)

In [33]:
! cat train.py

import dataclasses
import logging
import os
import pprint
from contextlib import ExitStack
from pathlib import Path
from typing import TYPE_CHECKING

import fire
import torch.cuda
import torch.distributed as dist
from mistral_common.tokens.tokenizers.mistral import MistralTokenizer
from torch.optim import AdamW, lr_scheduler

from finetune.args import TrainArgs
from finetune.checkpointing import Checkpointer
from finetune.data.data_loader import build_data_loader
from finetune.distributed import (
    BACKEND,
    avg_aggregate,
    get_rank,
    get_world_size,
    is_torchrun,
    set_device,
)
from finetune.eval import evaluate
from finetune.loss import compute_loss_with_mask
from finetune.mixed_precision import (
    downcast_mixed_precision,
    prepare_mixed_precision,
    upcast_mixed_precision,
)
from finetune.monitoring.metrics_logger import (
    MetricsLogger,
    eval_log_msg,
    get_eval_logs,
    get_train_logs,
    train_log_msg,
)
from finetune.monitoring.utils import 

In [34]:
%cd /workspace/working/mistral-finetune/

/workspace/working/mistral-finetune


/workspace/working/venv/lib/python3.10/site-packages/IPython/core/magics/osm.py:417: UserWarning: This is now an optional IPython functionality, setting dhist requires you to install the `pickleshare` library.
  self.shell.db['dhist'] = compress_dhist(dhist)[-100:]


In [35]:
!torchrun --nproc-per-node 1 -m train example/7B.yaml

args: TrainArgs(data=DataArgs(data='', shuffle=False, instruct_data='/workspace/working/data/NL_to_SPARQL_train.jsonl', eval_instruct_data='/workspace/working/data/NL_to_SPARQL_eval.jsonl', instruct=InstructArgs(shuffle=True, dynamic_chunk_fn_call=True)), model_id_or_path='/workspace/working/mistral_models', run_dir='outputs', optim=OptimArgs(lr=1e-05, weight_decay=0.1, pct_start=0.05), seed=0, num_microbatches=8, seq_len=2048, batch_size=1, max_norm=1.0, max_steps=300, log_freq=10, ckpt_freq=100, save_adapters=True, no_ckpt=False, num_ckpt_keep=3, eval_freq=100, no_eval=False, checkpoint=True, world_size=1, wandb=WandbArgs(project=None, offline=False, key=None, run_name=None), mlflow=MLFlowArgs(tracking_uri=None, experiment_name=None), lora=LoraArgs(enable=True, rank=16, dropout=0.0, scaling=16.0))
2025-03-27 23:59:21 (UTC) - 0:00:02 - distributed - INFO - torch.cuda.device_count: 1
2025-03-27 23:59:21 (UTC) - 0:00:02 - distributed - INFO - CUDA_VISIBLE_DEVICES: 0
2025-03-27 23:59:21 

In [36]:
%mv /workspace/working/mistral-finetune/outputs/ /workspace/working/
%ls /workspace/working/mistral-finetune/

LICENSE       example/   pyproject.toml        tests/      utils/
README.md     finetune/  requirements.dev.txt  train.py
__pycache__/  model/     requirements.txt      tutorials/


In [37]:
%cd /workspace/working/
%ls /workspace/working/

/workspace/working
data/              mistral-finetune-fyp.ipynb  outputs/
mistral-finetune/  mistral_models/             venv/


/workspace/working/venv/lib/python3.10/site-packages/IPython/core/magics/osm.py:417: UserWarning: This is now an optional IPython functionality, setting dhist requires you to install the `pickleshare` library.
  self.shell.db['dhist'] = compress_dhist(dhist)[-100:]


In [38]:
%cd /workspace/working/outputs/
%ls /workspace/working/outputs/
%cd /workspace/working/outputs/checkpoints/
%ls /workspace/working/outputs/checkpoints/
%cd /workspace/working/outputs/checkpoints/checkpoint_000300/
%ls /workspace/working/outputs/checkpoints/checkpoint_000300/
%cd /workspace/working/outputs/checkpoints/checkpoint_000300/consolidated/
%ls /workspace/working/outputs/checkpoints/checkpoint_000300/consolidated/
%pwd

/workspace/working/outputs
args.yaml  checkpoints/  metrics.eval.jsonl  metrics.train.jsonl  tb/


/workspace/working/venv/lib/python3.10/site-packages/IPython/core/magics/osm.py:417: UserWarning: This is now an optional IPython functionality, setting dhist requires you to install the `pickleshare` library.
  self.shell.db['dhist'] = compress_dhist(dhist)[-100:]


/workspace/working/outputs/checkpoints
checkpoint_000100/  checkpoint_000200/  checkpoint_000300/
/workspace/working/outputs/checkpoints/checkpoint_000300
consolidated/
/workspace/working/outputs/checkpoints/checkpoint_000300/consolidated
lora.safetensors  params.json  tokenizer.model.v3


'/workspace/working/outputs/checkpoints/checkpoint_000300/consolidated'

In [39]:
%cd /workspace/working/mistral-finetune/

/workspace/working/mistral-finetune


In [40]:
%pip install mistral_inference

Note: you may need to restart the kernel to use updated packages.


In [9]:
# with open("infer.py", "w") as file:
#     file.write('''import os
# import torch
# import torch.distributed as dist
# from mistral_inference.transformer import Transformer
# from mistral_inference.generate import generate
# from mistral_common.tokens.tokenizers.mistral import MistralTokenizer
# from mistral_common.protocol.instruct.messages import UserMessage
# from mistral_common.protocol.instruct.request import ChatCompletionRequest

# def main():
#     try:
#         # Initialize distributed process group
#         dist.init_process_group(backend='nccl')
#         local_rank = int(os.environ['LOCAL_RANK'])
#         torch.cuda.set_device(local_rank)
        
#         # Load tokenizer (each process does this)
#         if dist.get_rank() == 0:
#             print("Loading tokenizer...")
#         tokenizer_path = "/workspace/working/outputs/checkpoints/checkpoint_000300/consolidated/tokenizer.model.v3"
#         mistral_tokenizer = MistralTokenizer.from_file(tokenizer_path)
        
#         # Load base model with error handling
#         if dist.get_rank() == 0:
#             print("Loading base model...")
#         model_path = "/workspace/working/mistral_models"
#         try:
#             model = Transformer.from_folder(
#                 model_path, 
#                 dtype=torch.float16,
#                 device=torch.device(f"cuda:{local_rank}"),
#                 max_batch_size=3,
#                 num_pipeline_ranks=2
#             )
#         except Exception as e:
#             print(f"[Rank {dist.get_rank()}] Model loading failed: {e}")
#             raise
        
#         # Load LoRA adapter
#         if dist.get_rank() == 0:
#             print("Loading LoRA adapter...")
#         lora_path = "/workspace/working/outputs/checkpoints/checkpoint_000300/consolidated/lora.safetensors"
#         try:
#             model.load_lora(lora_path)
#         except Exception as e:
#             print(f"[Rank {dist.get_rank()}] LoRA loading failed: {e}")
#             raise
        
#         if dist.get_rank() == 0:
#             print(f"Model loaded on cuda:{local_rank}")
#             print("Running inference...")
#             prompt = "Who is the president of France?"
#             messages = [{"role": "user", "content": prompt}]
#             #tokens = mistral_tokenizer.encode_chat_completion(
#             #    ChatCompletionRequest(messages=[UserMessage(content=prompt)])
#             #).tokens
#             tokens = mistral_tokenizer.encode_chat_completion(
#                 ChatCompletionRequest(messages=messages)
#             ).tokens
            
#             out_tokens, _ = generate(
#                 [tokens], 
#                 model, 
#                 max_tokens=512,  # Reduced for testing
#                 temperature=0.3, 
#                 eos_id=mistral_tokenizer.instruct_tokenizer.tokenizer.eos_id
#             )
#             print(mistral_tokenizer.instruct_tokenizer.tokenizer.decode(out_tokens[0]))
        
#         dist.barrier()
        
#     except Exception as e:
#         print(f"[Rank {dist.get_rank()}] Error: {e}")
#         raise
#     finally:
#         if dist.is_initialized():
#             dist.destroy_process_group()

# if __name__ == "__main__":
#     # Set OMP_NUM_THREADS to avoid warning
#     os.environ['OMP_NUM_THREADS'] = '1'
#     main()
# ''')

In [21]:
import torch
import safetensors
from mistral_inference.transformer import Transformer
from mistral_inference.generate import generate
from mistral_common.tokens.tokenizers.mistral import MistralTokenizer
from mistral_common.protocol.instruct.messages import UserMessage
from mistral_common.protocol.instruct.request import ChatCompletionRequest

# load tokenizer
mistral_tokenizer = MistralTokenizer.from_file("/workspace/working/outputs/checkpoints/checkpoint_000300/consolidated/tokenizer.model.v3")
# load model
model = Transformer.from_folder("/workspace/working/mistral_models")
model.load_lora("/workspace/working/outputs/checkpoints/checkpoint_000300/consolidated/lora.safetensors")
safetensors.torch.save_model(model, "/workspace/working/outputs/finetunedmodel")

query = input("Any questions?\n")
prompt = f"Give just the SPARQL query over DBpedia Knowledge Graph for the given natural language query: {query}"
messages = [{"role" : "user", "content" : prompt}]
# chat completion request
completion_request = ChatCompletionRequest(messages=messages)

# encode message
tokens = mistral_tokenizer.encode_chat_completion(completion_request).tokens

# generate results
out_tokens, _ = generate([tokens], model, max_tokens=2048, temperature=0.50, eos_id=mistral_tokenizer.instruct_tokenizer.tokenizer.eos_id)

# decode generated tokens
result = mistral_tokenizer.instruct_tokenizer.tokenizer.decode(out_tokens[0])
print(result)
# ! cat infer.py

To retrieve the current president of India from the DBpedia Knowledge Graph, you can use the following SPARQL query:

```sparql
PREFIX dbo: <http://dbpedia.org/ontology/>
PREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>
PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
PREFIX xsd: <http://www.w3.org/2001/XMLSchema#>

SELECT DISTINCT ?president ?presidentLabel
WHERE {
  ?president a dbo:Person ;
         dbo:countryOfCitizenship dbo:India ;
         dbo:officeHolder dbo:PresidentOfIndia .
  SERVICE wikibus-labs:pageLabels { bd:serviceParam wikibuslabs:language "en" . }
  ?president rdfs:label ?presidentLabel .
}
ORDER BY DESC(STR(?presidentLabel))
LIMIT 1
```

This query searches for individuals who are a `dbo:Person`, have `dbo:countryOfCitizenship` as India, and hold the office of `dbo:PresidentOfIndia`. It also uses the Wikibus-labs service to retrieve the English labels for the results. The results are ordered in descending order by the label and limited to the top 1 res

In [22]:
from SPARQLWrapper import JSON, SPARQLWrapper
SPARQLendpt = SPARQLWrapper("http://dbpedia.org/sparql")
SPARQLendpt.setReturnFormat(JSON)
SPARQLendpt.setQuery('''PREFIX dbo: <http://dbpedia.org/ontology/>
PREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>
PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
PREFIX xsd: <http://www.w3.org/2001/XMLSchema#>

SELECT DISTINCT ?president ?presidentLabel
WHERE {
  ?president a dbo:Person ;
         dbo:countryOfCitizenship dbo:India ;
         dbo:officeHolder dbo:PresidentOfIndia .
  SERVICE wikibus-labs:pageLabels { bd:serviceParam wikibuslabs:language "en" . }
  ?president rdfs:label ?presidentLabel .
}
ORDER BY DESC(STR(?presidentLabel))
LIMIT 1''')
LLMAnswer = SPARQLendpt.query().convert()
LLMAnswer

QueryBadFormed: QueryBadFormed: A bad request has been sent to the endpoint: probably the SPARQL query is badly formed. 

Response:
b'Virtuoso 37000 Error SP030: SPARQL compiler, line 12: Undefined namespace prefix in prefix:localpart notation at \'wikibus-labs:pageLabels\' before \'{\'\n\nSPARQL query:\n#output-format:application/sparql-results+json\nPREFIX dbo: <http://dbpedia.org/ontology/>\nPREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>\nPREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>\nPREFIX xsd: <http://www.w3.org/2001/XMLSchema#>\n\nSELECT DISTINCT ?president ?presidentLabel\nWHERE {\n  ?president a dbo:Person ;\n         dbo:countryOfCitizenship dbo:India ;\n         dbo:officeHolder dbo:PresidentOfIndia .\n  SERVICE wikibus-labs:pageLabels { bd:serviceParam wikibuslabs:language "en" . }\n  ?president rdfs:label ?presidentLabel .\n}\nORDER BY DESC(STR(?presidentLabel))\nLIMIT 1\n'

Transformer(
  (tok_embeddings): Embedding(32768, 4096)
  (norm): RMSNorm()
  (output): Linear(in_features=4096, out_features=32768, bias=False)
  (layers): ModuleDict(
    (0): TransformerBlock(
      (attention): Attention(
        (wq): Linear(in_features=4096, out_features=4096, bias=False)
        (wk): Linear(in_features=4096, out_features=1024, bias=False)
        (wv): Linear(in_features=4096, out_features=1024, bias=False)
        (wo): Linear(in_features=4096, out_features=4096, bias=False)
      )
      (attention_norm): RMSNorm()
      (ffn_norm): RMSNorm()
      (feed_forward): FeedForward(
        (w1): Linear(in_features=4096, out_features=14336, bias=False)
        (w2): Linear(in_features=14336, out_features=4096, bias=False)
        (w3): Linear(in_features=4096, out_features=14336, bias=False)
      )
    )
    (1): TransformerBlock(
      (attention): Attention(
        (wq): Linear(in_features=4096, out_features=4096, bias=False)
        (wk): Linear(in_features=40

In [25]:
model.save()

AttributeError: 'Transformer' object has no attribute 'save'